In [1]:
import pandas as pd

from kaggle.api.kaggle_api_extended import KaggleApi
from sklearn.model_selection import train_test_split
from glob import glob

from preprocessing import preprocess_text

# Introduction:
This notebook aims to preprocess two datasets, the Disaster Tweet Dataset and the Fake/Real News Dataset, obtained from Kaggle using the Kaggle API. The goal is to bring both datasets into a consistent format with two columns: 'text' and 'label' **(0 for real, 1 for fake)**. The data will be split into train and test sets (80/20 ratio) and saved as CSV files.

Process Overview:
- **Dataset Acquisition:** Download the Disaster Tweet Dataset and Fake/Real News Dataset from Kaggle using the Kaggle API.
- **Dataset Preprocessing:** Ensure a consistent format by keeping only the 'text' column, assigning labels (0 for real, 1 for fake), and merging the datasets. The text column in both datasets will undergo preprocessing using a custom function called `preprocess_text`. This function applies various cleaning operations to the text, including URL and user mention removal, non-alphanumeric character removal, hashtag removal, punctuation removal, lowercase conversion, stop word removal and keeping only texts containing at least 3 words.
- **Train/Test Split:** Split the combined preprocessed dataset into train and test sets using an 80/20 ratio.
- **Save Preprocessed Data:** Save the preprocessed train and test datasets as separate CSV files.

# Disaster tweets

In [2]:
# Instantiate the Kaggle API object
api = KaggleApi()

# Set the Kaggle API credentials
api.authenticate()

In [3]:
# Set the dataset to download
disaster_dataset_slug = 'vstepanenko/disaster-tweets'
disaster_output_path = 'Data/disaster-tweets'

# Download the dataset files
api.dataset_download_files(disaster_dataset_slug, path=disaster_output_path, unzip=True)

In [4]:
disaster_path = list(glob(disaster_output_path + '*/*'))[0]

In [5]:
disaster_path

'Data/disaster-tweets/tweets.csv'

In [6]:
disaster = pd.read_csv(disaster_path)
disaster = disaster.drop(['id', 'keyword', 'location'], axis=1)

In [7]:
# Invert the values in the 'Target' column
disaster['target'] = disaster['target'].map({1: 0, 0: 1})
disaster = disaster.rename(columns={'target': 'label'})

In [8]:
disaster.head() # real: 0 | fake: 1

text  label
0  Communal violence in Bhainsa, Telangana. "Ston...      0
1  Telangana: Section 144 has been imposed in Bha...      0
2  Arsonist sets cars ablaze at dealership https:...      0
3  Arsonist sets cars ablaze at dealership https:...      0
4  "Lord Jesus, your love brings freedom and pard...      1

# Real/Fake News

In [9]:
# Set the dataset to download
news_dataset_slug = 'clmentbisaillon/fake-and-real-news-dataset'
news_output_path = 'Data/fake-and-real-news-dataset'

# Download the dataset files
api.dataset_download_files(news_dataset_slug, path=news_output_path, unzip=True)

In [10]:
news_path = list(glob(news_output_path + '*/*'))

In [11]:
news_path

['Data/fake-and-real-news-dataset/Fake.csv',
 'Data/fake-and-real-news-dataset/True.csv']

In [12]:
real_path = news_path[1]
fake_path = news_path[0]

In [13]:
real_news = pd.read_csv(real_path)
fake_news = pd.read_csv(fake_path)

In [14]:
real_news = real_news.drop(['title', 'subject', 'date'], axis=1)
fake_news = fake_news.drop(['title', 'subject', 'date'], axis=1)

In [15]:
real_news['label'] = 0
fake_news['label'] = 1

In [16]:
real_news.head()

text  label
0  WASHINGTON (Reuters) - The head of a conservat...      0
1  WASHINGTON (Reuters) - Transgender people will...      0
2  WASHINGTON (Reuters) - The special counsel inv...      0
3  WASHINGTON (Reuters) - Trump campaign adviser ...      0
4  SEATTLE/WASHINGTON (Reuters) - President Donal...      0

In [17]:
fake_news.head()

text  label
0  Donald Trump just couldn t wish all Americans ...      1
1  House Intelligence Committee Chairman Devin Nu...      1
2  On Friday, it was revealed that former Milwauk...      1
3  On Christmas day, Donald Trump announced that ...      1
4  Pope Francis used his annual Christmas Day mes...      1

# Concatenate the datasets

In [18]:
data = pd.concat([disaster, real_news, fake_news]).reset_index().drop(columns = 'index')

In [19]:
data.head()

text  label
0  Communal violence in Bhainsa, Telangana. "Ston...      0
1  Telangana: Section 144 has been imposed in Bha...      0
2  Arsonist sets cars ablaze at dealership https:...      0
3  Arsonist sets cars ablaze at dealership https:...      0
4  "Lord Jesus, your love brings freedom and pard...      1

# Preprocess the text

In [20]:
data = preprocess_text(data)

In [21]:
data.head()

text  label
0  communal violence bhainsa telangana stones pel...      0
1  telangana section 144 imposed bhainsa january ...      0
2               arsonist sets cars ablaze dealership      0
3               arsonist sets cars ablaze dealership      0
4  lord jesus love brings freedom pardon fill hol...      1

In [22]:
print(f'Percentage of REAL data: {round((len(data) - data["label"].sum()) / len(data) * 100, 2)}%')
print(f'Percentage of FAKE data: {round(data["label"].sum() / len(data) * 100, 2)}%')

Percentage of REAL data: 42.61%
Percentage of FAKE data: 57.39%


# Train/Test split and save

In [23]:
# Shuffle the DataFrame
shuffled_data = data.sample(frac=1, random_state=42)  # Set random_state for reproducibility

# Split the shuffled DataFrame into train and test sets
train_data, test_data = train_test_split(shuffled_data, test_size=0.2, random_state=42)  # Adjust test_size as needed

# Reset the index column
train_data = train_data.reset_index().drop(['index'], axis=1)
test_data = test_data.reset_index().drop(['index'], axis=1)

In [24]:
train_data.head()

text  label
0  name michael brown robbed local convenience st...      1
1  washington reuters japanese prime minister shi...      0
2  chicago reuters us house republican tax bill r...      0
3  reuters fbi interviewed michael flynn initial ...      0
4  harare reuters ousted zimbabwe finance ministe...      0

In [25]:
test_data.head()

text  label
0  kraig moss die hard donald trump supporter fol...      1
1  white house lawyers last month learned former ...      1
2  awesome many levels hard know beginafghanistan...      1
3  please note overwhelming information regarding...      1
4  kabul reuters us ambassador afghanistan said m...      0

In [26]:
# Save the train and test sets as separate CSV files
train_data.to_csv('Data/train_dataset.csv', index=False)
test_data.to_csv('Data/test_dataset.csv', index=False)